In [3]:
import warnings
warnings.filterwarnings('ignore')

## Instalação:

Para criar o ambiente com as ferramentas necessárias:

`conda create --name textrepr python=3 scikit-learn numpy scipy gensim nltk pandas jupyter ipython`

Para ativar o ambiente:

`source activate lconmeetings`

`pip install powerlaw`

Para executar o ambiente de programação, no mesmo diretório do arquivo Text Representations.ipynb digite:

`jupyter notebook`


In [2]:
import pandas as pd
import numpy as np
import sklearn.feature_extraction.text as txtfeats
import powerlaw
from nltk import skipgrams

In [4]:
tweets = pd.read_csv('tweets.csv.gz')
tweets.head()

Unnamed: 0        date      time  screen_name  \
0           0  2016-04-15  00:51:27  TierroDavid   
1           1  2016-04-15  00:52:20  TierroDavid   
2           2  2016-04-15  00:54:06  TierroDavid   
3           3  2016-04-15  00:11:32   lisadoflop   
4           4  2016-04-15  01:27:48  TierroDavid   

                                                text  
0  rt revistaepoca dilma diz que se resistir ao i...  
1  rt folha grupos pro e contra impeachment convo...  
2  estadao estadao irresponsavel patrocinando o g...  
3  lembrei de alguem com essa foto httpstcoxjwnbo...  
4  rt folha ministros sao exonerados para votarem...

In [6]:
bagofwords = txtfeats.CountVectorizer()
bow = bagofwords.fit_transform(tweets.text)

In [7]:
print(len(bagofwords.get_feature_names()))
bagofwords.get_feature_names()[5000:5010]

231602


['alemanharoubo',
 'alemanhas',
 'alemao',
 'alemaoe',
 'alemaofernando',
 'alemaomarau',
 'alempara',
 'alencar',
 'alencarinos',
 'alencarmariza']

In [9]:
avg = sum(len(t.split()) for t in tweets.text)/len(tweets.text)
print(avg)

16.223622447244896


In [43]:
print('O id de "alemanharoubo" é', bagofwords.vocabulary_.get('alemanharoubo'))
print('Total de {} atributos.'.format(len(bagofwords.vocabulary_)))

O id de "alemanharoubo" é 5000
Total de 231602 atributos.


In [10]:
novo_tweet = 'um novo tweet sobre um alemao kywz'

print(bagofwords.transform([novo_tweet]))

x = (bagofwords.transform([novo_tweet])
     .toarray()
     )

print('Índice das palavras presentes: ', x.nonzero()[1])
print()

for t in novo_tweet.split():
    print('O termo "{}" tem índice {}'.format(t, bagofwords.vocabulary_.get(t)))

print()
print('A frequência do termo "um" no documento é: ', x[0,226860])

print('Transformação inversa de x: ', bagofwords.inverse_transform(x)[0])

  (0, 5002)	1
  (0, 201288)	1
  (0, 220665)	1
  (0, 226539)	1
  (0, 226860)	2
Índice das palavras presentes:  [  5002 201288 220665 226539 226860]

O termo "um" tem índice 226860
O termo "novo" tem índice 201288
O termo "tweet" tem índice 226539
O termo "sobre" tem índice 220665
O termo "um" tem índice 226860
O termo "alemao" tem índice 5002
O termo "kywz" tem índice None

A frequência do termo "um" no documento é:  2
Transformação inversa de x:  ['alemao' 'novo' 'sobre' 'tweet' 'um']


### Outros parâmetros

`strip_accents : {‘ascii’, ‘unicode’, None}`: remove acentos das palavras com codificação ascii ou unicode (None por padrão).

`stop_words : string {‘english’}, list, or None (default)`: permite usar uma lista de *stop words* (None por padrão).

`lowercase : boolean, True by default`: transforma as letras em caixa baixa (padrão).

`binary : boolean, default=False`: não contabiliza a frequência dos termos (Falso por padrão).

### Luhn cut-off

`max_df : float in range [0.0, 1.0] or int, default=1.0`: remove os termos com frequência de documento maior que N.

`min_df : float in range [0.0, 1.0] or int, default=1`: remove os termos com frequência de documento menor que N.

`max_features : int or None, default=None`: seleciona os N atributos mais frequentes.

In [11]:
df = sorted(bow.sum(axis=0).A1)
fit = powerlaw.Fit(df)
cmp = fit.distribution_compare('power_law', 'exponential')
df_max = int(np.round(np.power(fit.xmin*np.power(2, 1/(fit.power_law.alpha-1)),4/3)))
df_min = int(np.round(np.power(fit.xmin*np.power(2, 1/(fit.power_law.alpha-1)),2/3)))

print('PL? (or EXP): ', cmp[1]<0.05)
print('alpha = ', fit.power_law.alpha)
print('df_min = {} df_max = {}'.format(df_min, df_max))

Calculating best minimal value for power law fit


PL? (or EXP):  True
alpha =  2.00175723834
df_min = 106 df_max = 11172


In [12]:
bagofwords = txtfeats.CountVectorizer(min_df=df_min, max_df=df_max, 
                                      strip_accents='unicode', stop_words=['e', 'ou', 'ele', 'ela'])
bow = bagofwords.fit_transform(tweets.text)
print('Total de {} atributos.'.format(len(bagofwords.vocabulary_)))

Total de 5333 atributos.


## N-grams

`analyzer : string, {‘word’, ‘char’, ‘char_wb’}`: se os n-grams serão determinados por palavras, por caracteres ou por caracteres dentro das palavras

`ngram_range : tuple (min_n, max_n)`: gera n-gramas com min_n <= n <= max_n

In [13]:
bagofwords = txtfeats.CountVectorizer(min_df=df_min, max_df=df_max, 
                                      strip_accents='unicode', ngram_range=(2,2))
bow = bagofwords.fit_transform(tweets.text)
print('Total de {} atributos.'.format(len(bagofwords.vocabulary_)))

Total de 10048 atributos.


In [9]:
tfidf = txtfeats.TfidfVectorizer()
bow = tfidf.fit_transform(tweets.text)

norm : ‘l1’, ‘l2’ or None, optional

Norm used to normalize term vectors. None for no normalization.

use_idf : boolean, default=True Enable inverse-document-frequency reweighting.

smooth_idf : boolean, default=True
Smooth idf weights by adding one to document frequencies, as if an extra document was seen containing every term in the collection exactly once. Prevents zero divisions.

sublinear_tf : boolean, default=False Apply sublinear tf scaling, i.e. replace tf with 1 + log(tf).

# Skipgram

`tfidf = txtfeats.TfidfVectorizer(tokenizer=skipgram)`

In [14]:
skip3n2grams = lambda s: skipgrams(s.split(), 2, 3)
tfidf = txtfeats.TfidfVectorizer(tokenizer=skip3n2grams, 
                                 min_df=df_min, max_df=df_max)
bow = tfidf.fit_transform(tweets.text)
print('Total de {} atributos.'.format(len(tfidf.vocabulary_)))

Total de 38330 atributos.


In [25]:
tfidf.get_feature_names()[10000:10010]

[('acovardado', 'mas'),
 ('acovardado', 'na'),
 ('acovardado', 'o'),
 ('acovardado', 'obriga'),
 ('acovardado', 'permitira'),
 ('acovardado', 'poder'),
 ('acovardado', 'povo'),
 ('acovardado', 'so'),
 ('acovardado', 'stf'),
 ('acovardado', 'tom')]

# MinHash

In [94]:
P = 109297
nhashes = 3
alphas = np.random.randint(1, P-1, (nhashes,))
betas  = np.random.randint(1, P-1, (nhashes,))

H = [list(map(hash,t.split())) for t in tweets.text[:100]]
MH = np.zeros((100,nhashes))

for i, h in enumerate(H):
    for j in range(nhashes):
        MH[i,j] = np.min(np.remainder(alphas[j]*h + betas[j], P))

In [95]:
MH[:10,:]

array([[  1.38460000e+04,   4.10000000e+01,   2.00000000e+01],
       [  1.53650000e+04,   8.05300000e+03,   9.03000000e+02],
       [  1.97050000e+04,   2.24230000e+04,   5.95900000e+03],
       [  1.44010000e+04,   4.05370000e+04,   4.59300000e+03],
       [  1.45870000e+04,   8.05300000e+03,   2.93200000e+03],
       [  1.36300000e+03,   6.01600000e+03,   5.33700000e+03],
       [  1.80000000e+03,   8.70800000e+03,   4.59300000e+03],
       [  1.92120000e+04,   3.05900000e+03,   4.59300000e+03],
       [  1.60000000e+02,   1.29300000e+04,   4.59300000e+03],
       [  3.04200000e+03,   8.70800000e+03,   2.46940000e+04]])

# Doc2Vec

In [68]:
from gensim.models import doc2vec

class LabeledLineSentence(object):
    def __init__(self, stream):
        self.stream = stream
    def __iter__(self):
        for uid, line in enumerate(self.stream):
            yield doc2vec.LabeledSentence(words=line.split(), tags=['SENT_%s' % uid])

In [70]:
model = doc2vec.Doc2Vec(LabeledLineSentence(tweets.text.values[:1000]))

In [71]:
X = model.docvecs

In [74]:
X[0][:10]

array([-0.00484932, -0.00559254,  0.00104118,  0.00191504, -0.00015034,
        0.00358489, -0.00116596,  0.00536888,  0.00067337,  0.00054678], dtype=float32)